In [14]:
import numpy as np
import pandas as pd

from neuclease.dvid import *
from neuclease.util import *

import hvplot.pandas

In [2]:
from neuclease import configure_default_logging
configure_default_logging()

In [4]:
ref_seg = ('emdata4:8450', '75d3ddd2e9e143a38fa9cc9e7d55b3d1', 'segmentation')
new_seg = ('emdata4:8460', '1ec355123bf94e588557a4568d26d258', 'segmentation')

#### TODO:

- generate updated mapping
- copy all label indexes (and remap IDs in transit)
- copy synapses
- copy annotations (hound Pat)
- copy focused proofreading keyvalue from the cloud server
- generate body meshes
- 

In [ ]:
all_bodies = []
start = 0

prog = tqdm_proxy()
prog.update(0)
while True:
    b = fetch_listlabels(*ref_seg, start, 10_000)
    if len(b) == 0:
        break
    all_bodies.append(b)
    start = b[-1]+1
    prog.update(len(b))

all_bodies = np.concatenate(bodies)

In [11]:
len(all_bodies)

104315

In [12]:
len(all_bodies[-1])

1

In [13]:
all_bodies[-1][-1]

841369754354

In [16]:
batch_sizes = pd.Series([*map(len, all_bodies)], name='num_labels')
batch_sizes.hvplot()

:Curve   [index]   (num_labels)

In [18]:
batch_sizes[batch_sizes == 1].iloc[0:1]

25763    1
Name: num_labels, dtype: int64

In [20]:
batch_sizes.iloc[25762:25764]

25762    9439
25763       1
Name: num_labels, dtype: int64

In [23]:
all_bodies[25762][-10:], all_bodies[25763][0]

(array([841369754344, 841369754345, 841369754346, 841369754347,
        841369754349, 841369754350, 841369754351, 841369754352,
        841369754353, 841369754354], dtype=uint64),
 841369754354)

In [22]:
start

841369754354

In [24]:
(np.array([*chain(*all_bodies[25763:])]) == 841369754354).all()

True

In [25]:
all([batch_a[-1] == batch_b[0] for batch_a, batch_b in zip(all_bodies[:-1], all_bodies[1:])])

True

In [29]:
fixed_batches = [batch[:-1] for batch in all_bodies] + [[all_bodies[-1][-1]]]

In [30]:
len(fixed_batches)

104316

In [31]:
batch_sizes = pd.Series([*map(len, fixed_batches)], name='num_labels')
batch_sizes.hvplot()

:Curve   [index]   (num_labels)

In [32]:
full_body_list = np.concatenate(fixed_batches)

In [33]:
full_body_list.shape

(257603677,)

In [34]:
pwd

'/groups/flyem/data/scratchspace/flyemflows/vnc-fullseg/february'

In [37]:
np.save('full-body-list-75d3d.npy', full_body_list)

In [42]:
mapping = fetch_complete_mappings(*ref_seg)

[2021-02-10 18:58:48,268] INFO Using kafka servers: ['kafka.int.janelia.org:9092', 'kafka2.int.janelia.org:9092', 'kafka3.int.janelia.org:9092']
[2021-02-10 18:58:48,269] INFO Reading kafka messages for topic: vncdvidrepo-adc102eea96740949971d0d4adb59d59-data-38ecc49915dc4c8ebdce4e7c494c8607
[2021-02-10 18:58:54,412] INFO Reading 51104 kafka messages took 6.1424946784973145 seconds
[2021-02-10 18:58:55,933] INFO Fetching http://emdata4:8450/api/node/75d3ddd2e9e143a38fa9cc9e7d55b3d1/segmentation/mappings?format=binary...
[2021-02-10 18:59:17,630] INFO Fetching http://emdata4:8450/api/node/75d3ddd2e9e143a38fa9cc9e7d55b3d1/segmentation/mappings?format=binary took 0:00:21.695828
[2021-02-10 18:59:17,631] INFO Constructing missing identity-mappings...
[2021-02-10 18:59:42,523] INFO Constructing missing identity-mappings took 0:00:24.891818


In [43]:
mapping.shape

(39464734,)

In [45]:
mapping.nunique()

4921543

In [46]:
full_body_list.min()

26374327

In [47]:
mapping.index.min()

40799632

In [50]:
import h5py
p = '/nrs/flyem/bergs/vnc-fullseg-november/download-rc5_wsexp-20201128.192112/sorted-by-body-sorted-by-segment-block-statistics.h5'
with h5py.File(p, 'r') as f:
    stats = f['stats'][:]

assert (stats['body_id'][:-1] <= stats['body_id'][1:]).all()

In [51]:
stats[:10]

array([(26374327, 26374327,  64, 4160, 21120,    80),
       (26374327, 26374327,  64, 4160, 21184,  2682),
       (26374327, 26374327, 128, 4096, 21120,  9360),
       (26374327, 26374327, 128, 4096, 21184, 22104),
       (26374327, 26374327, 128, 4160, 21120, 26480),
       (26374327, 26374327, 128, 4160, 21184, 62940),
       (26374327, 26374327, 192, 4160, 21120,    80),
       (26374327, 26374327, 192, 4160, 21184,   216),
       (26374328, 26374328,  64, 4160, 21184,   166),
       (26374328, 26374328,  64, 4160, 21248,    64)],
      dtype=[('body_id', '<u8'), ('segment_id', '<u8'), ('z', '<i4'), ('y', '<i4'), ('x', '<i4'), ('count', '<u4')])

In [ ]:
num_bodies = 1 + (stats['body_id'][1:] != stats['body_id'][:-1]).sum()

In [107]:
stats_bodies, stats_counts = group_sums_presorted(stats['count'][:, None].astype(np.uint64), stats['body_id'][:, None])

Aggregating 257587109 groups


In [108]:
stats_sizes = np.zeros_like(stats_bodies[:, 0], dtype=[('body', 'u8'), ('count', 'u8')])
stats_sizes['body'] = stats_bodies[:, 0]
stats_sizes['count'] = stats_counts[:, 0]

In [109]:
stats_sizes.sort(order=['count', 'body'])

In [110]:
_d = '/nrs/flyem/bergs/vnc-fullseg-november/download-rc5_wsexp-20201128.192112'
np.save(f'{_d}/rc5-agglo-body-sizes-descending.npy', stats_sizes[::-1])

In [115]:
pd.DataFrame(stats_sizes[-10:])

body         count
0   4657581493   35908450516
1   5071463468   36438970580
2   6295301863   39816196241
3  16922227881   40907469795
4  13706554606   42710226952
5   1279292982   57916307004
6    938906525   59625156531
7  30573515090   61295786977
8    136431578   78868176277
9  19882674229  108549580526

In [114]:
fetch_sizes('emdata4:8450', '9c78cca98d88456f99b0ef1cddbb8baa', 'segmentation', stats_sizes['body'][-10:])

body
4657581493      35802627118
5071463468      36427981115
6295301863      39812876269
16922227881     40905747594
13706554606     42661303431
1279292982      57683145767
938906525       59597007244
30573515090     61081923794
136431578       78867605405
19882674229    107604715946
Name: size, dtype: int64

In [116]:
msg_df = read_labelmap_kafka_df(*ref_seg)
cleaved_bodies = msg_df.query('action == "cleave"')['target_body']
new_bodies = [m['CleavedLabel'] for m in msg_df.query('action == "cleave"')['msg']]

[2021-02-10 23:02:22,660] INFO Using kafka servers: ['kafka.int.janelia.org:9092', 'kafka2.int.janelia.org:9092', 'kafka3.int.janelia.org:9092']
[2021-02-10 23:02:22,661] INFO Reading kafka messages for topic: vncdvidrepo-adc102eea96740949971d0d4adb59d59-data-38ecc49915dc4c8ebdce4e7c494c8607
[2021-02-10 23:02:28,399] INFO Reading 51220 kafka messages took 5.7377588748931885 seconds


In [119]:
top_bodies = set(stats_sizes['body'][-100_000:]) | set(cleaved_bodies) | set(new_bodies)

In [120]:
top_sizes = fetch_sizes(*ref_seg, sorted(top_bodies), processes=32, batch_size=100)

In [123]:
top_sizes = top_sizes.sort_values(ascending=False)

In [142]:
top90k = top_sizes.iloc[:90_000].rename_axis('orig_body').reset_index()

In [162]:
top90k['new_body'] = np.arange(10_000, 100_000, dtype=np.uint64)

In [147]:
top90k[['new_body', 'orig_body', 'size']].to_csv('top90k-1ec35.csv', index=False, header=True)

In [163]:
top90k.head()

orig_body         size  new_body
0   30573515090  42585373410     10000
1  841369745228  33410062049     10001
2  841369733104  29335518223     10002
3  841369732998  19530983691     10003
4  841369733054  19305136382     10004

In [152]:
# There should only be unmapped supervoxels if they're singleton bodies.
unmapped_top90 = pd.Index(top90k['orig_body']).difference(pd.Index(mapping.values))
unmapped_svcounts = pd.DataFrame([(body, len(fetch_supervoxels(*ref_seg, body))) for body in unmapped_top90], columns=['body', 'sv_count'])
assert (unmapped_svcounts['sv_count'] == 1).all()

In [167]:
# Make sure singletons are in the set we'll be mapping, even though they were elided from the original mapping
top_singleton_mapping = pd.Series(unmapped_top90.values, index=unmapped_top90, name='body').rename_axis('sv')
new_mapping = pd.concat((mapping, top_singleton_mapping)).rename('orig_body')
new_mapping = new_mapping.to_frame()

# orig -> new
top90_new_mapper = LabelMapper(top90k['orig_body'].values, top90k['new_body'].values)
new_mapping['new_body'] = top90_new_mapper.apply(new_mapping['orig_body'].values, True)

10000

In [177]:
top90k['size'].reset_index(drop=True).hvplot()

:Curve   [index]   (size)

In [182]:
def copy_labelindex_batch(bodies):
    indices = fetch_labelindices(*ref_seg, bodies)
    orig_labels = np.array([i.label for i in indices.indices], np.uint64)
    new_labels = top90_new_mapper.apply(orig_labels, True)
    for index, new_label in zip(indices.indices, new_labels):
        index.label = new_label
    
    post_labelindices(*new_seg, indices)

In [192]:
# Spot-check
copy_labelindex_batch(top90k['orig_body'].iloc[-10:])
o = fetch_labelindex(*ref_seg, top90k['orig_body'].iloc[-1], format='pandas').blocks
n = fetch_labelindex(*new_seg, top90k['new_body'].iloc[-1], format='pandas').blocks
assert (n.sort_values([*'zyx', 'sv']).reset_index(drop=True) == o.sort_values([*'zyx', 'sv']).reset_index(drop=True)).all().all()

In [ ]:
body_batches = iter_batches(full_body_list, 10_000)
compute_parallel(copy_labelindex_batch, body_batches, processes=32, ordered=False)

Process ForkPoolWorker-45:
Process ForkPoolWorker-61:
Process ForkPoolWorker-57:
Process ForkPoolWorker-40:
Process ForkPoolWorker-52:
Process ForkPoolWorker-63:
Process ForkPoolWorker-62:
Process ForkPoolWorker-47:
Process ForkPoolWorker-64:
Process ForkPoolWorker-58:
Process ForkPoolWorker-56:
Process ForkPoolWorker-37:
Process ForkPoolWorker-53:
Process ForkPoolWorker-41:
Process ForkPoolWorker-48:
Process ForkPoolWorker-46:
Process ForkPoolWorker-33:
Process ForkPoolWorker-59:
Process ForkPoolWorker-55:
Process ForkPoolWorker-54:
Process ForkPoolWorker-60:
Process ForkPoolWorker-38:
Process ForkPoolWorker-39:
Process ForkPoolWorker-42:
Process ForkPoolWorker-35:
Process ForkPoolWorker-50:
Process ForkPoolWorker-34:
Process ForkPoolWorker-49:
Process ForkPoolWorker-51:
Process ForkPoolWorker-36:
Process ForkPoolWorker-44:
Process ForkPoolWorker-43:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call las

In [ ]:
## TODO: Update mapping


In [ ]:
print('hi')